# Phase 3 - Joining the data
Trevor's [Phase 1](https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/1038316885899254/command/1038316885899255) and [Phase 2](https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/3816960191357033/command/3816960191357034) explorations were used as a base
<br> Architecture diagram courtesy of Esther

## Join Architecture Diagram
Below, we show the planned sequence of joins to join our 4 datasets (OpenFights, Stations, Airports, Weather) into the full dataset we plan to use for modeling.

This first diagram shows how we dealed with the missing airport and generated a mapping table containing closest single weather station for each airport.

![Joining_Process_1](files/shared_uploads/yuqiaochen@berkeley.edu/Joining_Process_1.png)

This second diagram shows all the joins we have performed to get our final fully joined dataset.

![Joining_Process_2](files/shared_uploads/yuqiaochen@berkeley.edu/Joining_Process_2.png)

## Imports

In [0]:
from pyspark.sql import types, functions as F
import pandas as pd
from pyspark.sql.functions import col, max
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number

## Configure Databricks blob access

In [0]:
blob_container = "main-storage" # The name of your container created in https://portal.azure.com
storage_account = "team05w261" # The name of your Storage account created in https://portal.azure.com
secret_scope = "team05" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "team05-key" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"

# Configure blob storage account access key globally
spark.conf.set(
  f"fs.azure.account.key.{storage_account}.blob.core.windows.net",
  dbutils.secrets.get(scope = secret_scope, key = secret_key)
)

In [0]:
display(dbutils.fs.ls(f"{mount_path}/datasets_final_project"))

path name size dbfs:/mnt/mids-w261/datasets_final_project/airlines/ airlines/ 0 dbfs:/mnt/mids-w261/datasets_final_project/airlines_data/ airlines_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/parquet_airlines_data/ parquet_airlines_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/parquet_airlines_data_3m/ parquet_airlines_data_3m/ 0 dbfs:/mnt/mids-w261/datasets_final_project/parquet_airlines_data_6m/ parquet_airlines_data_6m/ 0 dbfs:/mnt/mids-w261/datasets_final_project/stations_data/ stations_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/weather_data/ weather_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/weather_data_6_hr/ weather_data_6_hr/ 0 dbfs:/mnt/mids-w261/datasets_final_project/weather_data_single/ weather_data_single/ 0

## Read in datasets

In [0]:
###########################################
##### For FULL dataset, run this cell #####
###########################################

df_airlines = spark.read.parquet("/mnt/mids-w261/datasets_final_project/parquet_airlines_data/*")
df_stations = spark.read.parquet('dbfs:/mnt/mids-w261/datasets_final_project/stations_data/*')
df_weather = spark.read.parquet('dbfs:/mnt/mids-w261/datasets_final_project/weather_data/*')
open_flights = pd.read_csv("https://raw.githubusercontent.com/jpatokal/openflights/master/data/airports.dat", 
                           names = ['id','name', 'city', 'country', 'iata', 'icao', 'lat', 'lng', 'altitude', 
                                    'timezone', 'dst', 'tz_db_time_zone', 'type', 'source'])
open_flights = spark.createDataFrame(open_flights)

In [0]:
##############################################
##### For LIMITED dataset, run this cell #####
##############################################

df_airlines = spark.read.parquet("/mnt/mids-w261/datasets_final_project/parquet_airlines_data_3m/")
df_stations = spark.read.parquet('dbfs:/mnt/mids-w261/datasets_final_project/stations_data/*')
df_weather = spark.read.parquet('dbfs:/mnt/mids-w261/datasets_final_project/weather_data/*').filter(F.col('DATE') < "2015-04-01T00:00:00.000")
open_flights = pd.read_csv("https://raw.githubusercontent.com/jpatokal/openflights/master/data/airports.dat", 
                           names = ['id','name', 'city', 'country', 'iata', 'icao', 'lat', 'lng', 'altitude', 
                                    'timezone', 'dst', 'tz_db_time_zone', 'type', 'source'])
open_flights = spark.createDataFrame(open_flights)

In [0]:
# Full dataset row count

# df_airlines.count() # 63493682 rows
# df_stations.count() # 5004169 rows
# df_weather.count() # 630904436 rows
# open_flights.count() # 7698 rows

Out[14]: 7698

## Subset columns to those we are keeping and remove duplicates

In [0]:
# list the columns we're keeping
weather_col = ['STATION', 'SOURCE', 'DATE', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 
               'NAME', 'REPORT_TYPE', 'CALL_SIGN', 'QUALITY_CONTROL', 'WND', 
               'CIG', 'VIS', 'TMP', 'DEW', 'SLP', 'GA1', 'GF1', 'MA1', 'REM', 
               'AA1', 'AA2', 'AJ1', 'AL1', 'AN1', 'AO1', 'AU1', 'AT1']
airline_col = ["YEAR", "QUARTER", "MONTH", "DAY_OF_MONTH", "DAY_OF_WEEK", 
               "FL_DATE", "DEP_TIME", "DEP_TIME_BLK", "CRS_DEP_TIME", "CRS_ARR_TIME",
               "CRS_ELAPSED_TIME", "ARR_TIME", "ARR_TIME_BLK", "ACTUAL_ELAPSED_TIME",
               "ORIGIN", "ORIGIN_CITY_NAME", "ORIGIN_STATE_ABR", "ORIGIN_STATE_FIPS",
               "ORIGIN_STATE_NM", "ORIGIN_WAC",
               "DEST", "DEST_CITY_NAME", "DEST_STATE_ABR", "DEST_STATE_FIPS", 
               "DEST_STATE_NM","DEST_WAC",
               "OP_UNIQUE_CARRIER", "FLIGHTS", "DISTANCE", "DISTANCE_GROUP", "DIVERTED",
               "CANCELLED", "CANCELLATION_CODE", "CARRIER_DELAY", "DEP_DELAY", "DEP_DELAY_NEW",
               "DEP_DELAY_GROUP", "DEP_DEL15", "ARR_DELAY", "ARR_DELAY_NEW", "ARR_DELAY_GROUP",
               "ARR_DEL15", "WEATHER_DELAY", "NAS_DELAY", "SECURITY_DELAY", "LATE_AIRCRAFT_DELAY", "TAIL_NUM"]
station_col = ['station_id', 'wban', 'lat', 'lon', 'neighbor_id', 'neighbor_name', 'neighbor_state',
               'neighbor_call', 'neighbor_lat', 'neighbor_lon', 'distance_to_neighbor']
openfli_col = ['name', 'city', 'country', 'iata', 'lat', 'lng', 'icao', 'timezone', 'tz_db_time_zone']

In [0]:
# perform subsetting and drop duplicates
df_airlines = df_airlines.select(airline_col).dropDuplicates()
df_weather = df_weather.select(weather_col) # We did EDA and know there's no duplicate
df_stations = df_stations.select(station_col).dropDuplicates()
open_flights = open_flights.select(openfli_col).dropDuplicates()

In [0]:
# Filter out cancelled and diverted flights
df_airlines = df_airlines.filter((df_airlines.CANCELLED == 0) & (df_airlines.DIVERTED == 0))

In [0]:
df_airlines = df_airlines.drop('CANCELLED', 'DIVERTED', 'CANCELLATION_CODE')

## Prepping for a airport_weather_mapping

In [0]:
# select subset of columns
open_flights = open_flights.select('iata', 'icao', 'lat', 'lng', 'tz_db_time_zone')
print(open_flights.count())

# add 4 more airports
open_flights2 = spark.createDataFrame(pd.DataFrame({
    'iata': ['XWA', 'EAR', 'TKI', 'IFP'], 
    'icao': ['KXWA', 'KEAR', 'KTKI', 'KIFP'], 
    'lat': [48.2578135, 40.7274925, 33.1775399, 35.16558], 
    'lng': [-103.7418471, -99.0122646, -96.5926444, -114.557093], 
    'tz_db_time_zone': ['America/Chicago', 'America/Chicago', 'America/Chicago', 'America/Phoenix']
}))

# now union them
open_flights = open_flights.union(open_flights2)

# only need to keep the flights that are in df_airlines
origin_airports = df_airlines.select("origin").distinct().toPandas()
dest_airports = df_airlines.select("dest").distinct().toPandas()
all_airports = set(list(origin_airports.origin) + list(dest_airports.dest))
# do the filter
open_flights = open_flights.filter(F.col('iata').isin(all_airports))

open_flights.cache()

7698
Out[9]: DataFrame[iata: string, icao: string, lat: double, lng: double, tz_db_time_zone: string]

In [0]:
open_flights.createOrReplaceTempView("open_flights")
# 45,638 distinct weather stations
df_weather.select('latitude', 'longitude', 'station').distinct().createOrReplaceTempView('df_weather')

open_flights_closest_weather = spark.sql('''

with 

--step1: get every single combination between the two
-- and compute distance between. just use euclidean for now
tbl1 as (
    select
        a.iata
        ,a.icao
        ,a.lat lat_of
        ,a.lng lng_of
        ,b.latitude lat_w
        ,b.longitude lng_w
        ,b.station
        ,a.tz_db_time_zone
        ,power(power(a.lat - b.latitude,2) + power(a.lng - b.longitude,2),.5) as distance_euclidean
    from open_flights a 
    cross join df_weather b
)

--step2: the memory intensive sort to sort the distances for each airport
,tbl2 as(
    select
        tbl1.*
        ,dense_rank() over (partition by tbl1.iata order by tbl1.distance_euclidean) as n
    from tbl1
)

--step 3: filter to only include the 1 closest weather station. We could alternatively filter to include the top 3 closest weather stations and use that to take some sort of average if we want. 

select *
from tbl2
where n = 1
''')

# see a view of the whole thing:
display(open_flights_closest_weather)

# select a subset of columns to use as our "master mapping"
airport_weather_mapping = open_flights_closest_weather.select(['iata', 'icao', 'station', 'tz_db_time_zone'])
airport_weather_mapping.cache()

iata icao lat_of lng_of lat_w lng_w station tz_db_time_zone distance_euclidean n ATY KATY 44.91400146 -97.15470123 44.9047 -97.1494 72654614946 America/Chicago 0.010706082273388616 1 BGM KBGM 42.20869827 -75.97979736 42.2068 -75.98 72515004725 America/New_York 0.0019090552539127372 1 BUR KBUR 34.20069885253906 -118.35900115966795 34.20056 -118.3575 72288023152 America/Los_Angeles 0.0015075677020590299 1 DLG PADL 59.04470062 -158.5050049 59.05 -158.5167 70321025513 America/Anchorage 0.012839734903583469 1 DRT KDRT 29.3742008209 -100.927001953 29.3784 -100.927 72261022010 America/Chicago 0.004199179554159913 1 EUG KEUG 44.12459945678711 -123.21199798583984 44.1278 -123.2206 72693024221 America/Los_Angeles 0.00917813295116121 1 GEG KGEG 47.61989974975586 -117.53399658203124 47.6216 -117.528 72785024157 America/Los_Angeles 0.006232964539444569 1 GRB KGRB 44.48509979248047 -88.12960052490234 44.4794 -88.1366 72645014898 America/Chicago 0.009026643117081632 1 GRR KGRR 42.88079834 -85.52279663 42.8825 -85.52389 72635094860 America/New_York 0.002022647945760716 1 GTF KGTF 47.48199844 -111.3710022 47.4733 -111.3822 72775024143 America/Denver 0.014179336489177843 1 IDA KIDA 43.514599 -112.070999 43.519 -112.0639 72578524145 America/Denver 0.00835252069736824 1 IFP KIFP 35.16558 -114.557093 35.15722 -114.55944 72378853135 America/Phoenix 0.008683202692551701 1 INL KINL 48.566200256347656 -93.4030990600586 48.5614 -93.3981 72747014918 America/Chicago 0.00693058889796938 1 JLN KJLN 37.151798248291016 -94.49829864501952 37.15221 -94.49527 72349513987 America/Chicago 0.0030565061956528 1 LWB KLWB 37.8582992554 -80.3994979858 37.86667 -80.4 72412753801 America/New_York 0.008385784603449397 1 MSY KMSY 29.99340057373047 -90.25800323486328 29.99691 -90.27751 72231012916 America/Chicago 0.019819938416671158 1 PPG NSTU -14.3310003281 -170.710006714 -14.33056 -170.71361 91765061705 Pacific/Pago_Pago 0.0036300907472606426 1 PSE TJPS 18.00830078125 -66.56300354003906 18.008306 -66.563028 78520399999 America/Puerto_Rico 2.5010498611018982E-5 1 PSG PAPG 56.80170059 -132.9450073 56.8055 -132.9372 70386025329 America/Anchorage 0.008682709809617757 1 PVU KPVU 40.219200134277 -111.72299957275 40.21889 -111.72333 72572424174 America/Denver 4.5317263522566884E-4 1 SNA KSNA 33.67570114 -117.8679962 33.68 -117.86639 72297793184 America/Los_Angeles 0.00458912581431161 1 BTM KBTM 45.95479965209961 -112.49700164794922 45.9647 -112.5006 72774024135 America/Denver 0.010533993830935291 1 CID KCID 41.88470077514648 -91.71080017089844 41.8833 -91.7166 72545014990 America/Chicago 0.005966589362300746 1 COD KCOD 44.520198822 -109.024002075 44.51667 -109.01667 72670024045 America/Denver 0.00813707002017402 1 DCA KDCA 38.8521 -77.037697 38.8472 -77.03454 72405013743 America/New_York 0.005828949219191492 1 EAR KEAR 40.7274925 -99.0122646 40.73333 -99.0 72552614905 America/Chicago 0.013582960627563211 1 ESC KESC 45.7226982117 -87.0936965942 45.73333 -87.08333 72648094853 America/New_York 0.014849282735655027 1 FAR KFAR 46.92070007324219 -96.81580352783205 46.9253 -96.8111 72753014914 America/Chicago 0.006578943702761253 1 FNL KFNL 40.451804 -105.011 40.45 -105.01667 72476994035 America/Denver 0.005950068571042157 1 FSM KFSM 35.33660125732422 -94.36740112304688 35.333 -94.3625 72344013964 America/Chicago 0.006081945530493331 1 GSO KGSO 36.097801208496094 -79.93730163574219 36.0969 -79.9432 72317013723 America/New_York 0.005966814700602661 1 GTR KGTR 33.450298309299995 -88.5914001465 33.45 -88.58333 72330753893 America/Chicago 0.008075658051823207 1 LWS KLWS 46.3745002746582 -117.01499938964844 46.3747 -117.0156 72783024149 America/Los_Angeles 6.329478703387087E-4 1 MLU KMLU 32.51089859008789 -92.0376968383789 32.5155 -92.0405 72248613942 America/Chicago 0.005388013386511518 1 MQT KSAW 46.3535995483 -87.395401001 46.35 -87.4 72628494836 America/New_York 0.005840166073502174 1 MSN KMSN 43.13990020751953 -89.3375015258789 43.1405 -89.3452 72641014837 America/Chicago 0.007721803

Out[10]: DataFrame[iata: string, icao: string, station: string, tz_db_time_zone: string]

## Pre-processing the flight and weather data sets

In [0]:
# Adding an ID to the flights data
df_airlines = df_airlines.withColumn("id", F.monotonically_increasing_id())

# rename airports columns with suffix
old_col_nms = df_airlines.columns
new_col_nms = [var + '_AIRLNS' for var in old_col_nms]
for i in range(len(old_col_nms)):
  df_airlines = df_airlines.withColumnRenamed(old_col_nms[i], new_col_nms[i])
df_airlines.columns

Out[11]: ['YEAR_AIRLNS',
 'QUARTER_AIRLNS',
 'MONTH_AIRLNS',
 'DAY_OF_MONTH_AIRLNS',
 'DAY_OF_WEEK_AIRLNS',
 'FL_DATE_AIRLNS',
 'DEP_TIME_AIRLNS',
 'DEP_TIME_BLK_AIRLNS',
 'CRS_DEP_TIME_AIRLNS',
 'CRS_ARR_TIME_AIRLNS',
 'CRS_ELAPSED_TIME_AIRLNS',
 'ARR_TIME_AIRLNS',
 'ARR_TIME_BLK_AIRLNS',
 'ACTUAL_ELAPSED_TIME_AIRLNS',
 'ORIGIN_AIRLNS',
 'ORIGIN_CITY_NAME_AIRLNS',
 'ORIGIN_STATE_ABR_AIRLNS',
 'ORIGIN_STATE_FIPS_AIRLNS',
 'ORIGIN_STATE_NM_AIRLNS',
 'ORIGIN_WAC_AIRLNS',
 'DEST_AIRLNS',
 'DEST_CITY_NAME_AIRLNS',
 'DEST_STATE_ABR_AIRLNS',
 'DEST_STATE_FIPS_AIRLNS',
 'DEST_STATE_NM_AIRLNS',
 'DEST_WAC_AIRLNS',
 'OP_UNIQUE_CARRIER_AIRLNS',
 'FLIGHTS_AIRLNS',
 'DISTANCE_AIRLNS',
 'DISTANCE_GROUP_AIRLNS',
 'CARRIER_DELAY_AIRLNS',
 'DEP_DELAY_AIRLNS',
 'DEP_DELAY_NEW_AIRLNS',
 'DEP_DELAY_GROUP_AIRLNS',
 'DEP_DEL15_AIRLNS',
 'ARR_DELAY_AIRLNS',
 'ARR_DELAY_NEW_AIRLNS',
 'ARR_DELAY_GROUP_AIRLNS',
 'ARR_DEL15_AIRLNS',
 'WEATHER_DELAY_AIRLNS',
 'NAS_DELAY_AIRLNS',
 'SECURITY_DELAY_AIRLNS',
 'LATE_AIRCRAFT_DELAY_AIRLNS',
 'TAIL_NUM_AIRLNS',
 'id_AIRLNS']

In [0]:
# rename stations columns with suffix
old_col_nms = df_stations.columns
new_col_nms = [var + '_STNS' for var in old_col_nms]
for i in range(len(old_col_nms)):
  df_stations = df_stations.withColumnRenamed(old_col_nms[i], new_col_nms[i])
df_stations.columns


Out[12]: ['station_id_STNS',
 'wban_STNS',
 'lat_STNS',
 'lon_STNS',
 'neighbor_id_STNS',
 'neighbor_name_STNS',
 'neighbor_state_STNS',
 'neighbor_call_STNS',
 'neighbor_lat_STNS',
 'neighbor_lon_STNS',
 'distance_to_neighbor_STNS']

In [0]:
# rename weather columns with suffix
old_col_nms = df_weather.columns
new_col_nms = [var + '_WTHR' for var in old_col_nms]
for i in range(len(old_col_nms)):
  df_weather = df_weather.withColumnRenamed(old_col_nms[i], new_col_nms[i])
df_weather.columns



Out[13]: ['STATION_WTHR',
 'SOURCE_WTHR',
 'DATE_WTHR',
 'LATITUDE_WTHR',
 'LONGITUDE_WTHR',
 'ELEVATION_WTHR',
 'NAME_WTHR',
 'REPORT_TYPE_WTHR',
 'CALL_SIGN_WTHR',
 'QUALITY_CONTROL_WTHR',
 'WND_WTHR',
 'CIG_WTHR',
 'VIS_WTHR',
 'TMP_WTHR',
 'DEW_WTHR',
 'SLP_WTHR',
 'GA1_WTHR',
 'GF1_WTHR',
 'MA1_WTHR',
 'REM_WTHR',
 'AA1_WTHR',
 'AA2_WTHR',
 'AJ1_WTHR',
 'AL1_WTHR',
 'AN1_WTHR',
 'AO1_WTHR',
 'AU1_WTHR',
 'AT1_WTHR']

In [0]:
# # rename openflights columns with suffix

old_col_nms = open_flights.columns
new_col_nms = [var + '_OPNFLGHT' for var in old_col_nms]
for i in range(len(old_col_nms)):
  open_flights = open_flights.withColumnRenamed(old_col_nms[i], new_col_nms[i])
open_flights.columns

Out[14]: ['iata_OPNFLGHT',
 'icao_OPNFLGHT',
 'lat_OPNFLGHT',
 'lng_OPNFLGHT',
 'tz_db_time_zone_OPNFLGHT']

## Join part 1
  
- Join the mapping table containing closest single weather station for each airport with Weather table on StationID to get enriched Weather table with airport codes.

In [0]:
# Enrich the weather data with the airport mapping, essentially attach IATA code to each weather measurement
df_weather_origin = df_weather \
    .join(airport_weather_mapping, on=[df_weather.STATION_WTHR == airport_weather_mapping.station], how='inner')\
    .withColumn('DATE_WTHR_rounded', F.date_trunc("hour", F.col('DATE_WTHR')))

## Prepping 2 sets of weather data - origin and destination

In [0]:
# Copy the same data to construct the df_weather_dest dataframe and rename columns
df_weather_dest = df_weather_origin.toDF(*df_weather_origin.columns)
old_col_nms = df_weather_dest.columns
new_col_nms = [var + '_dest' for var in old_col_nms]
for i in range(len(old_col_nms)):
  df_weather_dest = df_weather_dest.withColumnRenamed(old_col_nms[i], new_col_nms[i])
  
df_weather_dest.columns

Out[16]: ['STATION_WTHR_dest',
 'SOURCE_WTHR_dest',
 'DATE_WTHR_dest',
 'LATITUDE_WTHR_dest',
 'LONGITUDE_WTHR_dest',
 'ELEVATION_WTHR_dest',
 'NAME_WTHR_dest',
 'REPORT_TYPE_WTHR_dest',
 'CALL_SIGN_WTHR_dest',
 'QUALITY_CONTROL_WTHR_dest',
 'WND_WTHR_dest',
 'CIG_WTHR_dest',
 'VIS_WTHR_dest',
 'TMP_WTHR_dest',
 'DEW_WTHR_dest',
 'SLP_WTHR_dest',
 'GA1_WTHR_dest',
 'GF1_WTHR_dest',
 'MA1_WTHR_dest',
 'REM_WTHR_dest',
 'AA1_WTHR_dest',
 'AA2_WTHR_dest',
 'AJ1_WTHR_dest',
 'AL1_WTHR_dest',
 'AN1_WTHR_dest',
 'AO1_WTHR_dest',
 'AU1_WTHR_dest',
 'AT1_WTHR_dest',
 'iata_dest',
 'icao_dest',
 'station_dest',
 'tz_db_time_zone_dest',
 'DATE_WTHR_rounded_dest']

In [0]:
# Go back and rename the origin columns
# rename some weather columns
old_col_nms = df_weather_origin.columns
new_col_nms = [var + '_origin' for var in old_col_nms]
for i in range(len(old_col_nms)):
  df_weather_origin = df_weather_origin.withColumnRenamed(old_col_nms[i], new_col_nms[i])
  
df_weather_origin.columns

Out[17]: ['STATION_WTHR_origin',
 'SOURCE_WTHR_origin',
 'DATE_WTHR_origin',
 'LATITUDE_WTHR_origin',
 'LONGITUDE_WTHR_origin',
 'ELEVATION_WTHR_origin',
 'NAME_WTHR_origin',
 'REPORT_TYPE_WTHR_origin',
 'CALL_SIGN_WTHR_origin',
 'QUALITY_CONTROL_WTHR_origin',
 'WND_WTHR_origin',
 'CIG_WTHR_origin',
 'VIS_WTHR_origin',
 'TMP_WTHR_origin',
 'DEW_WTHR_origin',
 'SLP_WTHR_origin',
 'GA1_WTHR_origin',
 'GF1_WTHR_origin',
 'MA1_WTHR_origin',
 'REM_WTHR_origin',
 'AA1_WTHR_origin',
 'AA2_WTHR_origin',
 'AJ1_WTHR_origin',
 'AL1_WTHR_origin',
 'AN1_WTHR_origin',
 'AO1_WTHR_origin',
 'AU1_WTHR_origin',
 'AT1_WTHR_origin',
 'iata_origin',
 'icao_origin',
 'station_origin',
 'tz_db_time_zone_origin',
 'DATE_WTHR_rounded_origin']

In [0]:
# create a timestamp feature
df_airlines = df_airlines.withColumn('datetime_dep', 
    F.unix_timestamp(F.concat(
        F.col('FL_DATE_AIRLNS'), 
        F.lit(' '), 
        F.lpad(F.col('CRS_DEP_TIME_AIRLNS'), 4, '0')
        ), 'yyyy-MM-dd HHmm').cast(types.TimestampType())
    )

# bring time-zones 
df_airlines_pre_join = df_airlines\
  .join(open_flights.select(['iata_OPNFLGHT', 'tz_db_time_zone_OPNFLGHT']).distinct(), on=[df_airlines.ORIGIN_AIRLNS == open_flights.iata_OPNFLGHT], how='left')\
  .withColumn("utc_dep", F.to_utc_timestamp(F.col("datetime_dep"), F.col("tz_db_time_zone_OPNFLGHT")))\
  .withColumn("utc_dep_3hrs_prior", F.col('utc_dep') - F.expr('INTERVAL 3 HOURS')) \
  .withColumn("utc_dep_3hrs_prior_rounded", F.date_trunc("hour", F.col('utc_dep_3hrs_prior'))) \
  .withColumn("utc_arrive", col("utc_dep") + (col("CRS_ELAPSED_TIME_AIRLNS") * F.expr("Interval 1 Minutes")))


In [0]:
df_airlines_pre_join.drop('iata_OPNFLGHT', 'tz_db_time_zone_OPNFLGHT')

Out[19]: DataFrame[YEAR_AIRLNS: int, QUARTER_AIRLNS: int, MONTH_AIRLNS: int, DAY_OF_MONTH_AIRLNS: int, DAY_OF_WEEK_AIRLNS: int, FL_DATE_AIRLNS: string, DEP_TIME_AIRLNS: int, DEP_TIME_BLK_AIRLNS: string, CRS_DEP_TIME_AIRLNS: int, CRS_ARR_TIME_AIRLNS: int, CRS_ELAPSED_TIME_AIRLNS: double, ARR_TIME_AIRLNS: int, ARR_TIME_BLK_AIRLNS: string, ACTUAL_ELAPSED_TIME_AIRLNS: double, ORIGIN_AIRLNS: string, ORIGIN_CITY_NAME_AIRLNS: string, ORIGIN_STATE_ABR_AIRLNS: string, ORIGIN_STATE_FIPS_AIRLNS: int, ORIGIN_STATE_NM_AIRLNS: string, ORIGIN_WAC_AIRLNS: int, DEST_AIRLNS: string, DEST_CITY_NAME_AIRLNS: string, DEST_STATE_ABR_AIRLNS: string, DEST_STATE_FIPS_AIRLNS: int, DEST_STATE_NM_AIRLNS: string, DEST_WAC_AIRLNS: int, OP_UNIQUE_CARRIER_AIRLNS: string, FLIGHTS_AIRLNS: double, DISTANCE_AIRLNS: double, DISTANCE_GROUP_AIRLNS: int, CARRIER_DELAY_AIRLNS: double, DEP_DELAY_AIRLNS: double, DEP_DELAY_NEW_AIRLNS: double, DEP_DELAY_GROUP_AIRLNS: int, DEP_DEL15_AIRLNS: double, ARR_DELAY_AIRLNS: double, ARR_DELAY_NEW_AIRLNS: double, ARR_DELAY_GROUP_AIRLNS: int, ARR_DEL15_AIRLNS: double, WEATHER_DELAY_AIRLNS: double, NAS_DELAY_AIRLNS: double, SECURITY_DELAY_AIRLNS: double, LATE_AIRCRAFT_DELAY_AIRLNS: double, TAIL_NUM_AIRLNS: string, id_AIRLNS: bigint, datetime_dep: timestamp, utc_dep: timestamp, utc_dep_3hrs_prior: timestamp, utc_dep_3hrs_prior_rounded: timestamp, utc_arrive: timestamp]

## Final join

- Join the weather tables onto the flight table at both origin and destination
- The weather is between 2 to 3 hours before scheduled departure at the weather station closest to the airport

In [0]:
# Join -- without the window function but with rounded timing
df_full_5 = df_airlines_pre_join \
  .join(df_weather_origin, on=[df_airlines_pre_join.utc_dep_3hrs_prior_rounded == df_weather_origin.DATE_WTHR_rounded_origin, df_airlines_pre_join.ORIGIN_AIRLNS == df_weather_origin.iata_origin], how='left') \
  .join(df_weather_dest, on=[df_airlines_pre_join.utc_dep_3hrs_prior_rounded == df_weather_dest.DATE_WTHR_rounded_dest, df_airlines_pre_join.DEST_AIRLNS == df_weather_dest.iata_dest], how='left')

# Now multiple weather station data could be joined to the same flight on either origin or dest - need to reduce that to only 1
windowSpec = Window.partitionBy("id_AIRLNS").orderBy(F.expr("bigint(DATE_WTHR_origin) - bigint(DATE_WTHR_rounded_origin) + bigint(DATE_WTHR_dest) - bigint(DATE_WTHR_rounded_dest)"))

df_full_5_dedup = df_full_5 \
  .withColumn("row_number", row_number().over(windowSpec)) \
  .filter("row_number == 1")


## Write to blob - this is checkpoint 1

In [0]:
# df_full_5_dedup.write.parquet(f"{blob_url}/2015_q1_full_join_5")

#df_full_5_dedup.write.parquet(f"{blob_url}/all_time_full_join_1") # Old version

df_full_5_dedup.write.parquet(f"{blob_url}/all_time_full_join_2") # New version: Included TAIL_NUM from Flight Dataset, filtered out Cancelled and diverted flights, created utc_arrive

# Data processing continues

In [0]:
%run ./dataclean_functions

In [0]:
# Reading from blob after checkpointing
#df_full_joined = spark.read.parquet(f"{blob_url}/all_time_full_join_1")
df_full_joined = spark.read.parquet(f"{blob_url}/all_time_full_join_2")


In [0]:
print(df_full_joined.count())
display(df_full_joined)

31178801

YEAR_AIRLNS QUARTER_AIRLNS MONTH_AIRLNS DAY_OF_MONTH_AIRLNS DAY_OF_WEEK_AIRLNS FL_DATE_AIRLNS DEP_TIME_AIRLNS DEP_TIME_BLK_AIRLNS CRS_DEP_TIME_AIRLNS CRS_ARR_TIME_AIRLNS CRS_ELAPSED_TIME_AIRLNS ARR_TIME_AIRLNS ARR_TIME_BLK_AIRLNS ACTUAL_ELAPSED_TIME_AIRLNS ORIGIN_AIRLNS ORIGIN_CITY_NAME_AIRLNS ORIGIN_STATE_ABR_AIRLNS ORIGIN_STATE_FIPS_AIRLNS ORIGIN_STATE_NM_AIRLNS ORIGIN_WAC_AIRLNS DEST_AIRLNS DEST_CITY_NAME_AIRLNS DEST_STATE_ABR_AIRLNS DEST_STATE_FIPS_AIRLNS DEST_STATE_NM_AIRLNS DEST_WAC_AIRLNS OP_UNIQUE_CARRIER_AIRLNS FLIGHTS_AIRLNS DISTANCE_AIRLNS DISTANCE_GROUP_AIRLNS CARRIER_DELAY_AIRLNS DEP_DELAY_AIRLNS DEP_DELAY_NEW_AIRLNS DEP_DELAY_GROUP_AIRLNS DEP_DEL15_AIRLNS ARR_DELAY_AIRLNS ARR_DELAY_NEW_AIRLNS ARR_DELAY_GROUP_AIRLNS ARR_DEL15_AIRLNS WEATHER_DELAY_AIRLNS NAS_DELAY_AIRLNS SECURITY_DELAY_AIRLNS LATE_AIRCRAFT_DELAY_AIRLNS TAIL_NUM_AIRLNS id_AIRLNS datetime_dep iata_OPNFLGHT tz_db_time_zone_OPNFLGHT utc_dep utc_dep_3hrs_prior utc_dep_3hrs_prior_rounded utc_arrive STATION_WTHR_origin SOURCE_WTHR_origin DATE_WTHR_origin LATITUDE_WTHR_origin LONGITUDE_WTHR_origin ELEVATION_WTHR_origin NAME_WTHR_origin REPORT_TYPE_WTHR_origin CALL_SIGN_WTHR_origin QUALITY_CONTROL_WTHR_origin WND_WTHR_origin CIG_WTHR_origin VIS_WTHR_origin TMP_WTHR_origin DEW_WTHR_origin SLP_WTHR_origin GA1_WTHR_origin GF1_WTHR_origin MA1_WTHR_origin REM_WTHR_origin AA1_WTHR_origin AA2_WTHR_origin AJ1_WTHR_origin AL1_WTHR_origin AN1_WTHR_origin AO1_WTHR_origin AU1_WTHR_origin AT1_WTHR_origin iata_origin icao_origin station_origin tz_db_time_zone_origin DATE_WTHR_rounded_origin STATION_WTHR_dest SOURCE_WTHR_dest DATE_WTHR_dest LATITUDE_WTHR_dest LONGITUDE_WTHR_dest ELEVATION_WTHR_dest NAME_WTHR_dest REPORT_TYPE_WTHR_dest CALL_SIGN_WTHR_dest QUALITY_CONTROL_WTHR_dest WND_WTHR_dest CIG_WTHR_dest VIS_WTHR_dest TMP_WTHR_dest DEW_WTHR_dest SLP_WTHR_dest GA1_WTHR_dest GF1_WTHR_dest MA1_WTHR_dest REM_WTHR_dest AA1_WTHR_dest AA2_WTHR_dest AJ1_WTHR_dest AL1_WTHR_dest AN1_WTHR_dest AO1_WTHR_dest AU1_WTHR_dest AT1_WTHR_dest iata_dest icao_dest station_dest tz_db_time_zone_dest DATE_WTHR_rounded_dest row_number 2016 2 4 21 4 2016-04-21 1924 1900-1959 1921 2230 369.0 2213 2200-2259 349.0 EWR Newark, NJ NJ 34 New Jersey 21 SEA Seattle, WA WA 53 Washington 93 UA 1.0 2402.0 10 null 3.0 3.0 0 0.0 -17.0 0.0 -2 0.0 null null null null N78448 948 2016-04-21T19:21:00.000+0000 EWR America/New_York 2016-04-21T23:21:00.000+0000 2016-04-21T20:21:00.000+0000 2016-04-21T20:00:00.000+0000 2016-04-22T05:30:00.000+0000 72502014734 7 2016-04-21T20:51:00.000+0000 40.6825 -74.1694 2.1 NEWARK LIBERTY INTERNATIONAL AIRPORT, NJ US FM-15 KEWR V030 220,5,N,0072,5 07620,5,M,N 016093,5,N,5 +0233,5 +0067,5 10147,5 02,5,+06096,5,99,9 99,99,9,99,9,99,9,06096,1,99,9,99,9 10149,5,10138,5 MET11404/21/16 15:51:02 METAR KEWR 212051Z 22014G18KT 10SM FEW200 BKN250 23/07 A2997 RMK AO2 SLP147 T02330067 56031 (DH) 01,0000,9,5 EWR KEWR 72502014734 America/New_York 2016-04-21T20:00:00.000+0000 72793024233 7 2016-04-21T20:53:00.000+0000 47.4444 -122.3138 112.8 SEATTLE TACOMA INTERNATIONAL AIRPORT, WA US FM-15 KSEA V030 210,5,N,0031,5 22000,5,9,N 016093,5,N,5 +0206,5 +0067,5 10084,5 02,5,+01067,5,99,9 02,99,5,99,9,99,9,01067,1,99,9,99,9 10078,5,09921,5 MET11804/21/16 12:53:02 METAR KSEA 212053Z 21006KT 10SM FEW035 FEW120 FEW250 21/07 A2976 RMK AO2 SLP084 T02060067 58016 (RS) 01,0000,9,5 SEA KSEA 72793024233 America/Los_Angeles 2016-04-21T20:00:00.000+0000 1 2016 2 4 1 5 2016-04-01 1742 1600-1659 1630 1900 150.0 2005 1900-1959 143.0 FLL Fort Lauderdale, FL FL 12 Florida 33 DCA Washington, DC VA 51 Virginia 38 WN 1.0 899.0 4 31.0 72.0 72.0 4 1.0 65.0 65.0 4 1.0 0.0 0.0 0.0 34.0 N713SW 1021 2016-04-01T16:30:00.000+0000 FLL America/New_York 2016-04-01T20:30:00.000+0000 2016-04-01T17:30:00.000+0000 2016-04-01T17:00:00.000+0000 2016-04-01T23:00:00.000+0000 74783012849 7 2016-04-01T17:53:00.000+0000 26.07875 -80.16217 3.4 FORT LAUDERDALE INTERNATIONAL AIRPORT, FL US FM-15 KFLL V030 160,5,N,0062,5 22000,5,9,N 016093,5,N,5

In [0]:
df_clean = generate_columns(df_full_joined)
df_clean_1 = drop_qc_columns(df_clean)
df_clean_2 = impute_weather_num(df_clean_1)
df_clean_3 = make_binary_cat_cols(df_clean_2)

KeyError with AU1_WTHR_combination_indicator_code_origin (categorical var)
KeyError with FLIGHTS_AIRLNS (categorical var)
KeyError with AA2_WTHR_condition_code_dest (categorical var)
KeyError with GF1_WTHR_total_lowest_cloud_cover_code_dest (categorical var)
KeyError with tz_db_time_zone_origin (categorical var)
KeyError with ORIGIN_STATE_ABR_AIRLNS (categorical var)
KeyError with LATE_AIRCRAFT_DELAY_AIRLNS (categorical var)
KeyError with AT1_WTHR_weather_type_dest (categorical var)
KeyError with tz_db_time_zone_OPNFLGHT (categorical var)
KeyError with LONGITUDE_WTHR_origin (categorical var)
KeyError with AU1_WTHR_obscuration_code_origin (categorical var)
KeyError with AA2_WTHR_condition_code_origin (categorical var)
KeyError with STATION_WTHR_dest (categorical var)
KeyError with ORIGIN_STATE_FIPS_AIRLNS (categorical var)
KeyError with DEP_DEL15_AIRLNS (categorical var)
KeyError with CRS_ELAPSED_TIME_AIRLNS (categorical var)
KeyError with ORIGIN_CITY_NAME_AIRLNS (categorical var)
KeyError with ARR_TIME_AIRLNS (categorical var)
KeyError with REPORT_TYPE_WTHR_origin (categorical var)
KeyError with NAME_WTHR_dest (categorical var)
KeyError with DATE_WTHR_rounded_origin (categorical var)
KeyError with DEST_AIRLNS (categorical var)
KeyError with CIG_WTHR_ceiling_determination_code_origin (categorical var)
KeyError with DEST_STATE_NM_AIRLNS (categorical var)
KeyError with iata_OPNFLGHT (categorical var)
KeyError with AU1_WTHR_descriptor_code_origin (categorical var)
KeyError with DATE_WTHR_origin (categorical var)
KeyError with DEP_DELAY_GROUP_AIRLNS (categorical var)
KeyError with AU1_WTHR_descriptor_code_dest (categorical var)
KeyError with station_origin (categorical var)
KeyError with SOURCE_WTHR_origin (categorical var)
KeyError with NAME_WTHR_origin (categorical var)
KeyError with AA1_WTHR_condition_code_origin (categorical var)
KeyError with QUALITY_CONTROL_WTHR_dest (categorical var)
KeyError with CIG_WTHR_CAVOK_code_dest (categorical var)
KeyError with TAIL_NUM_AIRLNS (categorical var)
KeyError with AN1_WTHR_condition_code_dest (categorical var)
KeyError with CIG_WTHR_CAVOK_code_origin (categorical var)
KeyError with DEST_STATE_FIPS_AIRLNS (categorical var)
KeyError with iata_origin (categorical var)
KeyError with AT1_WTHR_weather_type_origin (categorical var)
KeyError with DEST_WAC_AIRLNS (categorical var)
KeyError with DAY_OF_MONTH_AIRLNS (categorical var)
KeyError with iata_dest (categorical var)
KeyError with CIG_WTHR_ceiling_determination_code_dest (categorical var)
KeyError with OP_UNIQUE_CARRIER_AIRLNS (categorical var)
KeyError with ACTUAL_ELAPSED_TIME_AIRLNS (categorical var)
KeyError with ORIGIN_STATE_NM_AIRLNS (categorical var)
KeyError with id_AIRLNS (categorical var)
KeyError with SECURITY_DELAY_AIRLNS (categorical var)
KeyError with YEAR_AIRLNS (categorical var)
KeyError with AU1_WTHR_precipitation_code_origin (categorical var)
KeyError with station_dest (categorical var)
KeyError with DAY_OF_WEEK_AIRLNS (categorical var)
KeyError with DEP_TIME_AIRLNS (categorical var)
KeyError with GA1_WTHR_coverage_code_origin (categorical var)
KeyError with STATION_WTHR_origin (categorical var)
KeyError with AU1_WTHR_precipitation_code_dest (categorical var)
KeyError with LONGITUDE_WTHR_dest (categorical var)
KeyError with ARR_DELAY_NEW_AIRLNS (categorical var)
KeyError with ELEVATION_WTHR_origin (categorical var)
KeyError with DEST_STATE_ABR_AIRLNS (categorical var)
KeyError with ARR_DEL15_AIRLNS (categorical var)
KeyError with NAS_DELAY_AIRLNS (categorical var)
KeyError with datetime_dep (categorical var)
KeyError with AU1_WTHR_combination_indicator_code_dest (categorical var)
KeyError with CRS_ARR_TIME_AIRLNS (categorical var)
KeyError with ORIGIN_WAC_AIRLNS (categorical var)
KeyError with FL_DATE_AIRLNS (categorical var)
KeyError with icao_origin (categorical var)
KeyError with ARR_TIME_BLK_AIRLNS (categorical var)
KeyError with REPORT_TYPE_WTHR_dest (categorical var)
KeyError with LATITUDE_WTHR_origin (categorical var)

In [0]:
# Generate flight derived features 
# (Calling flight_derived_features_creation function from ./working_notebooks/derived_features_function_esther)

df_clean_4 = flight_derived_features_creation(df_clean_3)

In [0]:
display(df_clean_4)

YEAR_AIRLNS QUARTER_AIRLNS MONTH_AIRLNS DAY_OF_MONTH_AIRLNS DAY_OF_WEEK_AIRLNS FL_DATE_AIRLNS DEP_TIME_AIRLNS DEP_TIME_BLK_AIRLNS CRS_DEP_TIME_AIRLNS CRS_ARR_TIME_AIRLNS CRS_ELAPSED_TIME_AIRLNS ARR_TIME_AIRLNS ARR_TIME_BLK_AIRLNS ACTUAL_ELAPSED_TIME_AIRLNS ORIGIN_AIRLNS ORIGIN_CITY_NAME_AIRLNS ORIGIN_STATE_ABR_AIRLNS ORIGIN_STATE_FIPS_AIRLNS ORIGIN_STATE_NM_AIRLNS ORIGIN_WAC_AIRLNS DEST_AIRLNS DEST_CITY_NAME_AIRLNS DEST_STATE_ABR_AIRLNS DEST_STATE_FIPS_AIRLNS DEST_STATE_NM_AIRLNS DEST_WAC_AIRLNS OP_UNIQUE_CARRIER_AIRLNS FLIGHTS_AIRLNS DISTANCE_AIRLNS DISTANCE_GROUP_AIRLNS CARRIER_DELAY_AIRLNS DEP_DELAY_AIRLNS DEP_DELAY_NEW_AIRLNS DEP_DELAY_GROUP_AIRLNS DEP_DEL15_AIRLNS ARR_DELAY_AIRLNS ARR_DELAY_NEW_AIRLNS ARR_DELAY_GROUP_AIRLNS ARR_DEL15_AIRLNS WEATHER_DELAY_AIRLNS NAS_DELAY_AIRLNS SECURITY_DELAY_AIRLNS LATE_AIRCRAFT_DELAY_AIRLNS TAIL_NUM_AIRLNS id_AIRLNS datetime_dep iata_OPNFLGHT tz_db_time_zone_OPNFLGHT utc_dep utc_dep_3hrs_prior utc_dep_3hrs_prior_rounded utc_arrive STATION_WTHR_origin SOURCE_WTHR_origin DATE_WTHR_origin LATITUDE_WTHR_origin LONGITUDE_WTHR_origin ELEVATION_WTHR_origin NAME_WTHR_origin REPORT_TYPE_WTHR_origin CALL_SIGN_WTHR_origin QUALITY_CONTROL_WTHR_origin iata_origin icao_origin station_origin tz_db_time_zone_origin DATE_WTHR_rounded_origin STATION_WTHR_dest SOURCE_WTHR_dest DATE_WTHR_dest LATITUDE_WTHR_dest LONGITUDE_WTHR_dest ELEVATION_WTHR_dest NAME_WTHR_dest REPORT_TYPE_WTHR_dest CALL_SIGN_WTHR_dest QUALITY_CONTROL_WTHR_dest iata_dest icao_dest station_dest tz_db_time_zone_dest DATE_WTHR_rounded_dest row_number WND_WTHR_direction_angle_origin WND_WTHR_speed_rate_origin CIG_WTHR_ceiling_height_dimension_origin VIS_WTHR_distance_dimension_origin TMP_WTHR_air_temperature_origin DEW_WTHR_dew_point_temperature_origin SLP_WTHR_sea_level_pressure_origin GA1_WTHR_base_height_dimension_origin GF1_WTHR_lowest_cloud_base_height_dimension_origin MA1_WTHR_altimeter_setting_rate_origin MA1_WTHR_station_pressure_rate_origin AA1_WTHR_period_quantity_in_hours_origin AA1_WTHR_depth_dimension_origin AA2_WTHR_period_quantity_in_hours_origin AA2_WTHR_depth_dimension_origin AJ1_WTHR_dimension_origin AJ1_WTHR_equivalent_water_depth_dimension_origin AL1_WTHR_period_quantity_origin AL1_WTHR_depth_dimension_origin AN1_WTHR_period_quantity_origin AN1_WTHR_depth_dimension_origin AO1_WTHR_period_quantity_in_minutes_origin AO1_WTHR_depth_dimension_origin WND_WTHR_direction_angle_dest WND_WTHR_speed_rate_dest CIG_WTHR_ceiling_height_dimension_dest VIS_WTHR_distance_dimension_dest TMP_WTHR_air_temperature_dest DEW_WTHR_dew_point_temperature_dest SLP_WTHR_sea_level_pressure_dest GA1_WTHR_base_height_dimension_dest GF1_WTHR_lowest_cloud_base_height_dimension_dest MA1_WTHR_altimeter_setting_rate_dest MA1_WTHR_station_pressure_rate_dest AA1_WTHR_period_quantity_in_hours_dest AA1_WTHR_depth_dimension_dest AA2_WTHR_period_quantity_in_hours_dest AA2_WTHR_depth_dimension_dest AJ1_WTHR_dimension_dest AJ1_WTHR_equivalent_water_depth_dimension_dest AL1_WTHR_period_quantity_dest AL1_WTHR_depth_dimension_dest AN1_WTHR_period_quantity_dest AN1_WTHR_depth_dimension_dest AO1_WTHR_period_quantity_in_minutes_dest AO1_WTHR_depth_dimension_dest WND_WTHR_type_code_origin-V WND_WTHR_type_code_origin-C WND_WTHR_type_code_origin-N WND_WTHR_type_code_origin-R WND_WTHR_type_code_origin-H CIG_WTHR_ceiling_determination_code_origin-M CIG_WTHR_ceiling_determination_code_origin-C CIG_WTHR_ceiling_determination_code_origin-W CIG_WTHR_CAVOK_code_origin-Y CIG_WTHR_CAVOK_code_origin-N GA1_WTHR_coverage_code_origin-00 GA1_WTHR_coverage_code_origin-01 GA1_WTHR_coverage_code_origin-02 GA1_WTHR_coverage_code_origin-03 GA1_WTHR_coverage_code_origin-04 GA1_WTHR_coverage_code_origin-05 GA1_WTHR_coverage_code_origin-06 GA1_WTHR_coverage_code_origin-07 GA1_WTHR_coverage_code_origin-08 GA1_WTHR_coverage_code_origin-09 GA1_WTHR_coverage_code_origin-10 GA1_WTHR_cloud_type_code_origin-00 GA1_WTHR_cloud_type_code_origin-01 GA1_WTHR_cloud_type_code_origin-02 GA1_WTHR_cloud_type_

In [0]:
columns_to_drop = [
  'DEP_TIME_AIRLNS',
  'DEP_TIME_BLK_AIRLNS',
  'ARR_TIME_AIRLNS',
  'ARR_TIME_BLK_AIRLNS',
  'ACTUAL_ELAPSED_TIME_AIRLNS',
  'ORIGIN_CITY_NAME_AIRLNS',
  'ORIGIN_STATE_ABR_AIRLNS',
  'ORIGIN_STATE_FIPS_AIRLNS',
  'ORIGIN_STATE_NM_AIRLNS',
  'ORIGIN_WAC_AIRLNS',
  'DEST_CITY_NAME_AIRLNS',
  'DEST_STATE_ABR_AIRLNS',
  'DEST_STATE_FIPS_AIRLNS',
  'DEST_STATE_NM_AIRLNS',
  'DEST_WAC_AIRLNS',
  'DISTANCE_GROUP_AIRLNS',
  'CARRIER_DELAY_AIRLNS',
  'DEP_DELAY_AIRLNS',
  'DEP_DELAY_NEW_AIRLNS',
  'DEP_DELAY_GROUP_AIRLNS',
  'ARR_DELAY_AIRLNS',
  'ARR_DELAY_NEW_AIRLNS',
  'ARR_DELAY_GROUP_AIRLNS',
  'ARR_DEL15_AIRLNS',
  'WEATHER_DELAY_AIRLNS',
  'NAS_DELAY_AIRLNS',
  'SECURITY_DELAY_AIRLNS',
  'LATE_AIRCRAFT_DELAY_AIRLNS',
  'TAIL_NUM_AIRLNS',
  'id_AIRLNS',
  'datetime_dep',
  'iata_OPNFLGHT',
  'tz_db_time_zone_OPNFLGHT',
  'utc_dep',
  'utc_dep_3hrs_prior',
  'utc_dep_3hrs_prior_rounded',
  'utc_arrive',
  'STATION_WTHR_origin',
  'SOURCE_WTHR_origin',
  'DATE_WTHR_origin',
  'NAME_WTHR_origin',
  'REPORT_TYPE_WTHR_origin',
  'CALL_SIGN_WTHR_origin',
  'QUALITY_CONTROL_WTHR_origin',
  'iata_origin',
  'icao_origin',
  'station_origin',
  'tz_db_time_zone_origin',
  'DATE_WTHR_rounded_origin',
  'STATION_WTHR_dest',
  'SOURCE_WTHR_dest',
  'DATE_WTHR_dest',
  'NAME_WTHR_dest',
  'REPORT_TYPE_WTHR_dest',
  'CALL_SIGN_WTHR_dest',
  'QUALITY_CONTROL_WTHR_dest',
  'iata_dest',
  'icao_dest',
  'station_dest',
  'tz_db_time_zone_dest',
  'DATE_WTHR_rounded_dest',
  'row_number'
]

In [0]:
df_clean_5 = df_clean_4.drop(*columns_to_drop)
df_clean_5.columns

Out[115]: ['YEAR_AIRLNS',
 'QUARTER_AIRLNS',
 'MONTH_AIRLNS',
 'DAY_OF_MONTH_AIRLNS',
 'DAY_OF_WEEK_AIRLNS',
 'FL_DATE_AIRLNS',
 'CRS_DEP_TIME_AIRLNS',
 'CRS_ARR_TIME_AIRLNS',
 'CRS_ELAPSED_TIME_AIRLNS',
 'ORIGIN_AIRLNS',
 'DEST_AIRLNS',
 'OP_UNIQUE_CARRIER_AIRLNS',
 'FLIGHTS_AIRLNS',
 'DISTANCE_AIRLNS',
 'DEP_DEL15_AIRLNS',
 'LATITUDE_WTHR_origin',
 'LONGITUDE_WTHR_origin',
 'ELEVATION_WTHR_origin',
 'LATITUDE_WTHR_dest',
 'LONGITUDE_WTHR_dest',
 'ELEVATION_WTHR_dest',
 'WND_WTHR_direction_angle_origin',
 'WND_WTHR_speed_rate_origin',
 'CIG_WTHR_ceiling_height_dimension_origin',
 'VIS_WTHR_distance_dimension_origin',
 'TMP_WTHR_air_temperature_origin',
 'DEW_WTHR_dew_point_temperature_origin',
 'SLP_WTHR_sea_level_pressure_origin',
 'GA1_WTHR_base_height_dimension_origin',
 'GF1_WTHR_lowest_cloud_base_height_dimension_origin',
 'MA1_WTHR_altimeter_setting_rate_origin',
 'MA1_WTHR_station_pressure_rate_origin',
 'AA1_WTHR_period_quantity_in_hours_origin',
 'AA1_WTHR_depth_dimension_origin',
 'AA2_WTHR_period_quantity_in_hours_origin',
 'AA2_WTHR_depth_dimension_origin',
 'AJ1_WTHR_dimension_origin',
 'AJ1_WTHR_equivalent_water_depth_dimension_origin',
 'AL1_WTHR_period_quantity_origin',
 'AL1_WTHR_depth_dimension_origin',
 'AN1_WTHR_period_quantity_origin',
 'AN1_WTHR_depth_dimension_origin',
 'AO1_WTHR_period_quantity_in_minutes_origin',
 'AO1_WTHR_depth_dimension_origin',
 'WND_WTHR_direction_angle_dest',
 'WND_WTHR_speed_rate_dest',
 'CIG_WTHR_ceiling_height_dimension_dest',
 'VIS_WTHR_distance_dimension_dest',
 'TMP_WTHR_air_temperature_dest',
 'DEW_WTHR_dew_point_temperature_dest',
 'SLP_WTHR_sea_level_pressure_dest',
 'GA1_WTHR_base_height_dimension_dest',
 'GF1_WTHR_lowest_cloud_base_height_dimension_dest',
 'MA1_WTHR_altimeter_setting_rate_dest',
 'MA1_WTHR_station_pressure_rate_dest',
 'AA1_WTHR_period_quantity_in_hours_dest',
 'AA1_WTHR_depth_dimension_dest',
 'AA2_WTHR_period_quantity_in_hours_dest',
 'AA2_WTHR_depth_dimension_dest',
 'AJ1_WTHR_dimension_dest',
 'AJ1_WTHR_equivalent_water_depth_dimension_dest',
 'AL1_WTHR_period_quantity_dest',
 'AL1_WTHR_depth_dimension_dest',
 'AN1_WTHR_period_quantity_dest',
 'AN1_WTHR_depth_dimension_dest',
 'AO1_WTHR_period_quantity_in_minutes_dest',
 'AO1_WTHR_depth_dimension_dest',
 'WND_WTHR_type_code_origin-V',
 'WND_WTHR_type_code_origin-C',
 'WND_WTHR_type_code_origin-N',
 'WND_WTHR_type_code_origin-R',
 'WND_WTHR_type_code_origin-H',
 'CIG_WTHR_ceiling_determination_code_origin-M',
 'CIG_WTHR_ceiling_determination_code_origin-C',
 'CIG_WTHR_ceiling_determination_code_origin-W',
 'CIG_WTHR_CAVOK_code_origin-Y',
 'CIG_WTHR_CAVOK_code_origin-N',
 'GA1_WTHR_coverage_code_origin-00',
 'GA1_WTHR_coverage_code_origin-01',
 'GA1_WTHR_coverage_code_origin-02',
 'GA1_WTHR_coverage_code_origin-03',
 'GA1_WTHR_coverage_code_origin-04',
 'GA1_WTHR_coverage_code_origin-05',
 'GA1_WTHR_coverage_code_origin-06',
 'GA1_WTHR_coverage_code_origin-07',
 'GA1_WTHR_coverage_code_origin-08',
 'GA1_WTHR_coverage_code_origin-09',
 'GA1_WTHR_coverage_code_origin-10',
 'GA1_WTHR_cloud_type_code_origin-00',
 'GA1_WTHR_cloud_type_code_origin-01',
 'GA1_WTHR_cloud_type_code_origin-02',
 'GA1_WTHR_cloud_type_code_origin-03',
 'GA1_WTHR_cloud_type_code_origin-04',
 'GA1_WTHR_cloud_type_code_origin-05',
 'GA1_WTHR_cloud_type_code_origin-06',
 'GA1_WTHR_cloud_type_code_origin-07',
 'GA1_WTHR_cloud_type_code_origin-08',
 'GA1_WTHR_cloud_type_code_origin-09',
 'GA1_WTHR_cloud_type_code_origin-10',
 'GA1_WTHR_cloud_type_code_origin-12',
 'GA1_WTHR_cloud_type_code_origin-15',
 'GF1_WTHR_total_coverage_code_origin-00',
 'GF1_WTHR_total_coverage_code_origin-01',
 'GF1_WTHR_total_coverage_code_origin-02',
 'GF1_WTHR_total_coverage_code_origin-03',
 'GF1_WTHR_total_coverage_code_origin-04',
 'GF1_WTHR_total_coverage_code_origin-05',
 'GF1_WTHR_total_coverage_code_origin-06',
 'GF1_WTHR_total_coverage_code_origin-07',
 'GF1_WTHR_total_coverage_code_origin-08',
 'GF1_WTHR_total_coverage_code_origin-09',
 'GF1_WTHR

### Checkpoint 2 - Data ready for modelling

In [0]:
df_clean_5.write.parquet(f"{blob_url}/all_time_full_join_6")